<h2>Sage Notebook zur Aufgabe<br />10.3 Dosenpendel</h2>
<p>der Vorlesung </p>
<p>    Theoretische Physik 1. Math Modellierung und Theor Mechanik<br />    Uni Leipzig, Sommersemester 2019<br />    Autor:  Jürgen Vollmer (2018)<br />    Lizenz:  Creative Commons Attribution-ShareAlike 4.0 International (CC BY-SA 4.0)<br />    see:  https://creativecommons.org/licenses/by-sa/4.0/deed.en</p>
<p><strong>Sage</strong> ist ein OpenSource Projekt, das viele Methoden der computerbasierten Mathe-<br />matik und Computer-Algebra in einem Python-basierten Notebook anbietet. <br /><strong>Dokumentation</strong> und Informationen zur <strong>Installation</strong> findet man auf<br />        https://sagemath.org<br />Eine hervorragende Einführung in das Arbeiten mit Sage bietet das Buch<br />        Paul Zimmermann, u.a.: "Computational Mathematics with SageMath"<br />        http://sagebook.gforge.inria.fr/english.html</p>
<h2>Allgemeine Definitionen, Variablen, Konstanten</h2>
<p>Pfad und Stammname für Abbildungen</p>
<p>Bitte den Pfad editiert und die Kommentarzeichen vor den "save_image()"-Befehlen entfernen, um die erstellten Dateien zu speichern.</p>

In [ ]:
# baseName = '../prob10_3__dosenPendel/'

<p>Pakete laden für Plotten und Numerik</p>

In [ ]:
import scipy; from scipy import integrate
import numpy as np

V = VectorSpace(RR, 2)

## Differentialgleichung als Funktion von $t$

In [ ]:
t = var('t')
kappa = var('kappa')

def dX_dt(X, t, kappa=0.5) :
    return [ X[1], -kappa/2 * (1+X[1]^2) * sin(X[0])/(1-kappa*cos(X[0]))]

## Trajektorien

### Funktion zum Berechnen der Trajektorien

In [ ]:
tMaxDefault = 10
tStep = 0.01

tValDefauls = srange(0, tMaxDefault, tStep)


def trajectories( kappa, ICs, tVals=tValDefauls ) :
    Xo = []
    for IC in  ICs:
        Xo.append( integrate.odeint( dX_dt, IC, tVals, args = (kappa,) ) )
    return Xo

### Plotten der Trajektorien

In [ ]:
# Anzahl Anfangsbedingungen
n = 10

# Anfangswinkel
thetaN = 1e-3

# Anfangsgeschwindigkeiten  (als Abweichung von der Homoklinen)
Vini = np.array([0.2, 0.5, 0.7, 0.8, 0.9, 0.99, 0.999, 0.9999, 0.99999, 1.00001, 1.0001, 1.001, 1.01, 1.03, 1.1, 1.2, 1.5, 2, 3])

# Parameter zum Setzen der Anfangsgeschwindigkeiten
Vmin = 0.5
Vmax = 2

## ----------------------------------------------------------------------
def trajectory_plot( kappa, tMax=tMaxDefault ) :

    yMin = -1
    yMax = 5

    ## Homokline berechnen
    tVals = np.arange(0, tMax, tStep)
    dotThetaN = sqrt( kappa * abs( (1+cos(thetaN)) / (1-kappa*cos(thetaN)) ) )
    IChom = [[thetaN, dotThetaN]]
    Xhom = trajectories(kappa, IChom, tVals=tVals)
    
    ## Bahnen berechnen   
    ICs = zip(np.ones_like(Vini)*thetaN, Vini*dotThetaN)
    Xos = trajectories(kappa, ICs, tVals=tVals)
    
    # Bahnen plotten
    p = Graphics()
    for Xo in Xos :   
        p += line( zip(tVals*sqrt(kappa/2)/np.pi, Xo[:,0]/np.pi), ymin=yMin, ymax=yMax )

    p += line( zip(tVals*sqrt(kappa/2)/np.pi, Xhom[0][:,0]/np.pi), ymin=yMin, ymax=yMax, color='green', thickness=3 )

    p.axes_labels( [r'$2 t/T_0$', r'$\theta/\pi$'] )
    return p

In [ ]:
# trajectory_plot( 0.2 )

<h2>Phasenraumplot mit Vektorfeld</h2>


### Anfangswerte für Bahnen im Phasenraum

In [ ]:
IC1 = srange(V([-2*pi+1e-6, 0]), V([     -1e-6, 0]), step=V([(2*pi-2e-6)/n,0]))
IC2 = srange(V([     +1e-6, 0]), V([ 2*pi-1e-6, 0]), step=V([(2*pi-2e-6)/n,0]))
IC3 = srange(V([ -pi,-1+1e-2]), V([-pi,1+1e-2]), step=V([ 0, 2/n]))
IC4 = srange(V([  pi,-1+1e-2]), V([ pi,1+1e-2]), step=V([ 0, 2/n]))

### Phasenraumplot

In [ ]:
x,y = var('x', 'y')

def phase_space_plot(kappa) :
    print "kappa = ", kappa
    ## Bahnen berechnen
    Xo1 = trajectories(kappa, IC1)
    Xo2 = trajectories(kappa, IC2)
    Xo3 = trajectories(kappa, IC3)
    Xo4 = trajectories(kappa, IC4)
    
    ## Homoclinen
    p   = plot(  sqrt(abs(kappa*(1+cos(x))/(1-kappa*cos(x)))), xmin=-2*pi, xmax=2*pi, color='green', thickness=3 )
    p  += plot( -sqrt(abs(kappa*(1+cos(x))/(1-kappa*cos(x)))), xmin=-2*pi, xmax=2*pi, color='green', thickness=3 )

    ## Bahnen
    for j in range(n) :   
        p += line( Xo1[j], xmin=-2*pi, xmax=2*pi, color='blue')
        p += line( Xo2[j], xmin=-2*pi, xmax=2*pi, color='blue')
        p += line( Xo3[j], xmin=-2*pi, xmax=2*pi, color='blue')
        p += line( Xo4[j], xmin=-2*pi, xmax=2*pi, color='blue')

    p.axes_labels( [r'$\theta$', r'$\dot\theta/\omega$'] )
    return p

### Theoriekurven im Phasenraum

In [ ]:
set_verbose(-1)
def theta_dot( theta, kappa, e ) :
    sqr = (e + kappa*cos(theta)) / (1-kappa*cos(theta))
    return sqrt(sqr)


def theoriekurven( kappa ) :
    p = Graphics()
    for delta in range( 21 ) :
        e = -kappa + 1e-3 * exp(delta/2)
        p += plot(  theta_dot( x, kappa, e ), xmin=-2*pi, xmax=2*pi, color='red' )
        p += plot( -theta_dot( x, kappa, e ), xmin=-2*pi, xmax=2*pi, color='red' )
        
    p.axes_labels( [r'$\theta$', r'$\dot\theta/\omega$'] )
    return p

# Abbildungen für diverse Parameterwerte
<h3> $\kappa = 0.999$</h3>

In [ ]:
# time scale adopted for out plots
tScale  =  sqrt(0.99/2)/np.pi

##  --------------------------------------------------------------------------
# parameter <thetaMax> is provided in multiples of pi
def quarterPeriod (thetaMax) :
    return 2*acosh(1/cos(thetaMax*pi/2))

##  --------------------------------------------------------------------------
# parameter <thetaMax> is provided in multiples of pi
def f_oscil (t, thetaMax) :

    # half period of oscillation
    halfJump = quarterPeriod(thetaMax).n()
    
    # theta(t) in multiples of pi
    if ( t < 2*halfJump ) : 
        return  (2/pi) * acos( cos(thetaMax*pi/2) * cosh( ( t-halfJump)/2 ) )
    else : 
        return  -(2/pi) * acos( cos(thetaMax*pi/2) * cosh( ( t-3*halfJump)/2 ) )

## oscillating trjectories
pOsc  = plot( lambda t: f_oscil(t/tScale, 0.99999), (t, 0, 4*quarterPeriod(0.99)), color='green', thickness=4 )
pOsc += plot( lambda t: f_oscil(t/tScale, 0.98), (t, 0, 4*quarterPeriod(0.99)), color='red', thickness=4 )
pOsc += plot( lambda t: f_oscil(t/tScale, 0.715), (t, 0, 4*quarterPeriod(0.73)), color='red', thickness=4 )
pOsc += plot( lambda t: f_oscil(t/tScale, 0.495), (t, 0, 6*quarterPeriod(0.51)), color='red', thickness=4 )
pOsc += plot( lambda t: f_oscil(t/tScale, 0.13), (t, 0, 6*quarterPeriod(0.21)), color='red', thickness=4 )

show(pOsc, xmax=3, ymax=1.5, axes_labels=[r'$2 t/T_0$', r'$\theta/\pi$'] )

In [ ]:
##  --------------------------------------------------------------------------
# parameter <thetaMax> is provided in multiples of pi
def quarterPeriodRun (thetaMax) :
    return 2*asinh(1/Amp)

##  --------------------------------------------------------------------------
# parameter  <Amp>  sets velocity 
def f_run (t, Amp ) :
    
    # period of oscillation
    halfJump =  2*asinh(1/Amp)
    
    # theta(t) in multiples of pi
    if ( t < 2*halfJump ) : 
        return   (2/pi) * (pi-acos( Amp * sinh( (t-  halfJump)/2 )) )
    else :
        return 2+(2/pi) * (pi-acos( Amp * sinh( (t-3*halfJump)/2 )) )

## running trjectories
pRun  = plot( lambda t: f_run(t/tScale, 0.03), (t, 0, 4*quarterPeriod(0.99)), color='red', thickness=4 )
pRun += plot( lambda t: f_run(t/tScale, 0.14), (t, 0, 4*quarterPeriod(0.99)), color='red', thickness=4 )
pRun += plot( lambda t: f_run(t/tScale, 0.245 ), (t, 0, 4*quarterPeriod(0.73)), color='red', thickness=4 )
pRun += plot( lambda t: f_run(t/tScale, 0.455), (t, 0, 6*quarterPeriod(0.51)), color='red', thickness=4 )
pRun += plot( lambda t: f_run(t/tScale, 0.66), (t, 0, 6*quarterPeriod(0.51)), color='red', thickness=4 )
pRun += plot( lambda t: f_run(t/tScale, 1.11 ), (t, 0, 6*quarterPeriod(0.21)), color='red', thickness=4 )

show(pOsc + pRun , xmax=3, ymax=5, axes_labels=[r'$2 t/T_0$', r'$\theta/\pi$'])

In [ ]:
kappa = 0.999

## Trajektorien plotten
qTrajectories = trajectory_plot( kappa )
q0_999 = pOsc + pRun + qTrajectories
q0_999.set_axes_range(xmax=3, ymax=4 )
q0_999.axes_labels( [r'$2 t/T_0$', r'$\theta/\pi$'] )

## Phasenraumplot berechnen
p0_999  = phase_space_plot( kappa )
p0_999 += theoriekurven(    kappa )
p0_999.set_axes_range(ymin=-20, ymax=20)
p0_999.axes_labels([r'$\theta$', r'$\dot\theta/\omega$'])

# Abbildungen zeigen
plt = graphics_array([q0_999, p0_999])
show(plt, figsize=[8,6])

# Abbildung speichern
# plt.save_image(baseName+'kappa_0_999.svg', figsize=[9,4])

## $\kappa = 0.99$

In [ ]:
kappa = 0.99

## Trajektorien plotten
q0_990 = trajectory_plot( kappa )
q0_990.set_axes_range(ymax=4)

## Phasenraumplot berechnen
p0_990  = phase_space_plot( kappa )
p0_990 += theoriekurven(    kappa )
p0_990.set_axes_range(ymin=-20, ymax=20)
p0_990.axes_labels([r'$\theta$', r'$\dot\theta/\omega$'])

# Abbildungen zeigen
plt = graphics_array([q0_990, p0_990])
show(plt, figsize=[8,6])

# Abbildung speichern
# plt.save_image(baseName+'kappa_0_990.svg', figsize=[9,4])

## $\kappa = 0.9$

In [ ]:
kappa = 0.9

## Trajektorien plotten
q0_900 = trajectory_plot( kappa )
q0_900.set_axes_range(ymax=4)

## Graphen berechnen
p0_900  = phase_space_plot(kappa )
p0_900 += theoriekurven(   kappa )
p0_900.set_axes_range(ymin=-10, ymax=10)
p0_900.axes_labels([r'$\theta$', r'$\dot\theta/\omega$'])

# Abbildung zeigen
plt = graphics_array([q0_990, p0_990])
show(plt, figsize=[8,6])

# Abbildung speichern
# plt.save_image(baseName+'kappa_0_900.svg', figsize=[9,4])

<h3> $\kappa = 0.8$</h3>

In [ ]:
kappa = 0.8

## Trajektorien plotten
q0_800 = trajectory_plot( kappa )
q0_800.set_axes_range(ymax=5)

## Graphen berechnen
p0_800  = phase_space_plot(kappa )
p0_800 += theoriekurven(   kappa )
p0_800.set_axes_range(ymin=-6, ymax=6)
p0_800.axes_labels([r'$\theta$', r'$\dot\theta/\omega$'])

# Abbildung zeigen
plt = graphics_array((q0_800, p0_800))
show(plt, figsize=[8,6])

# Abbildung speichern
# plt.save_image(baseName+'kappa_0_800.svg', figsize=[9,4])

<h3> $\kappa = 0.5$</h3>

In [ ]:
kappa = 0.5

## Trajektorien plotten
q0_500 = trajectory_plot( kappa, tMax=20 )
q0_500.set_axes_range(ymax=5)

## Graphen berechnen
p0_500  = phase_space_plot(kappa )
p0_500 += theoriekurven(   kappa )
p0_500.set_axes_range(ymin=-3, ymax=3)
p0_500.axes_labels([r'$\theta$', r'$\dot\theta/\omega$'])

# Abbildung zeigen
plt = graphics_array((q0_500, p0_500))
show(plt, figsize=[8,6])

# Abbildung speichern
# plt.save_image(baseName+'kappa_0_500.svg', figsize=[9,4])

<h3> $\kappa = 0.2$</h3>

In [ ]:
kappa = 0.2

## Trajektorien plotten
q0_200 = trajectory_plot( kappa, tMax=30 )
q0_200.set_axes_range(ymax=5)

## Graphen berechnen
p0_200  = phase_space_plot(kappa )
p0_200 += theoriekurven(   kappa )
p0_200.set_axes_range(ymin=-2, ymax=2)
p0_200.axes_labels([r'$\theta$', r'$\dot\theta/\omega$'])

# Abbildung zeigen
plt = graphics_array((q0_200, p0_200))
show(plt, figsize=[8,6])

# Abbildung speichern
# plt.save_image(baseName+'kappa_0_200.svg', figsize=[9,4])

<h3> $\kappa = 0.01$</h3>

In [ ]:
kappa = 0.01

## Trajektorien plotten
q0_010  = trajectory_plot( kappa, tMax=200 )
q0_010 += plot(0.2*sin(x*pi), x, 0, 4, color='red', thickness=3)
q0_010.set_axes_range(xmax=4, ymax=5)
q0_010.axes_labels([r'$2 t/T_0$', r'$\theta/\pi$'])

## Graphen berechnen
p0_010  = phase_space_plot(kappa )
p0_010 += theoriekurven(   kappa )
p0_010.set_axes_range(ymin=-1, ymax=1)
p0_010.axes_labels([r'$\theta$', r'$\dot\theta/\omega$'])

# Abbildung zeigen
plt = graphics_array((q0_010, p0_010))
show(plt, figsize=[8,6])

# Abbildung speichern
# plt.save_image(baseName+'kappa_0_010.svg', figsize=[9,4])